In [1]:
import time
import numpy as np
import pandas as pd
import community as community_louvain
import networkx as nx
import pycombo
from sklearn.cluster import SpectralClustering

import torch
import torch.optim as optim
import torch.nn as nn
import torch.nn.functional as F
torch.set_printoptions(sci_mode=False)

import warnings
warnings.filterwarnings("ignore") 

# Utils

In [2]:
def get_network(net_name):
    if net_name == 'karate':
        network = nx.karate_club_graph()
    elif net_name == 'Les Miserables':
        network = nx.les_miserables_graph()
    else:
        network = nx.read_pajek('../data/'+net_name+'.net').to_undirected()
    return network

def get_all_networks():
    net_names=["karate", "Les Miserables", "David Copperfield","Jazz Musicians","Dolphins Social Network"]
    graphs = [(get_network(net_name), net_name) for net_name in net_names]
    return graphs

In [3]:
def normalize(adj):
    adj = torch.FloatTensor(adj)
    adj_id = torch.FloatTensor(torch.eye(adj.shape[1]))
    adj = adj + adj_id
    rowsum = torch.FloatTensor(adj.sum(-1))
    degree_mat_inv_sqrt = torch.diag_embed(torch.float_power(rowsum,-0.5), dim1=-2, dim2=-1).float()
    adj_norm = torch.mm(degree_mat_inv_sqrt.T, torch.mm(adj, degree_mat_inv_sqrt))
    return adj_norm

def modularity_matrix(adj):
    w_in = adj.sum(dim=0, keepdim=True)
    w_out = adj.sum(dim=1, keepdim=True)
    T = w_out.sum()
    Q = adj / T - w_out * w_in / T ** 2
    return Q

def modularity(C,Q):
    Q1 = torch.mm(C.T, Q)
    Q2 = torch.mm(Q1, C)
    M = torch.trace(Q2)
    return -M

def doublerelu(x):
    return torch.clamp(x, 0, 1)

In [4]:
def is_binary(C):
    sums = C.sum(dim=1, keepdim=True)
    maxs = C.max(dim=1, keepdim=True).values
    mins = C.min(dim=1, keepdim=True).values
    zeros = torch.zeros(sums.shape)
    ones = torch.ones(sums.shape)
    if torch.all(sums == ones) and torch.all(maxs == ones) and torch.all(mins == zeros):
        return True, "all binary"
    else:
        return False, "{} non-binary out of {}".format(torch.sum(~((sums == ones) & (maxs == ones) & (mins == zeros))).item(), C.shape[0])

def test_is_binary():
    C = np.array([[0,0,1],[0.999,0.001,0],[1,0,0]])
    C = torch.FloatTensor(C)
    print(is_binary(C))
    C = np.array([[0,0,1],[1,0.000,0],[1,0,0]])
    C = torch.FloatTensor(C)
    print(is_binary(C))
    C = np.array([[-0.5,0.5,1],[1,0.000,0],[1,0,0]])
    C = torch.FloatTensor(C)
    print(is_binary(C))

#test_is_binary()

In [5]:
def move_gains_old_slow_reliable_version(C, Q):
    node_max_gain = np.zeros([C.shape[0]])
    is_bin, ratio_nonbin = is_binary(C)
    if not is_bin:
        print("community is not binary")
        return ratio_nonbin, "{} nodes could be moved with total gain {}".format(sum(node_max_gain > 0), node_max_gain.sum())
    current_modularity = -modularity(C,Q)
    for node in range(C.shape[0]):
        current_community = C[node, :].max(0).indices.item()
        C[node, current_community] = 0
        for new_community in range(C.shape[2]):
            if new_community == current_community:
                continue
            C[node, new_community] = 1
            new_modularity = -modularity(C,Q)
            diff = current_modularity - new_modularity
            diff2 = Q[node,:] @ (C[0, :, current_community] - C[:, new_community]) + Q[node,node] + \
                    (C[:, current_community] - C[:, new_community]) @ Q[:,node] + Q[node,node]
            C[node, new_community] = 0
            if abs(diff.item() - diff2.item()) > 1e-6:
                print("diff != diff2", diff, diff2, node, new_community)
            if diff2 < 0:
                print("move node {} from {} to {} to gain {}".format(node, current_community, new_community, -diff2.item()))
                node_max_gain[node] = max(node_max_gain[node], -diff2.item())
        C[node, current_community] = 1
    return ratio_nonbin, "{} nodes could be moved with total gain {}".format(sum(node_max_gain > 0), node_max_gain.sum())

def move_gains(C, Q, verbosity=2):
    node_max_gain = np.zeros([C.shape[0]])
    non_bin = 0
    moveable_nonbin = 0
    Q2 = (Q + Q.T) * (1 - torch.eye(Q.shape[0]))
    for node in range(C.shape[0]):
        current_community = C[node, :].max(0).indices.item()
        max_prob = C[node, current_community].item()
        if max_prob < 1:
            non_bin += 1
            current_modularity = -modularity(C, Q)
            for new_community in range(C.shape[1]):
                old_val = torch.clone(C[node, :])
                C[node, :] = torch.zeros([C.shape[1]])
                C[node, new_community] = 1
                new_modularity = -modularity(C,Q)
                diff = new_modularity - current_modularity
                C[node, :] = old_val
                if verbosity > 1 and diff > 0:
                    print("move node {} from {} (curr. prob. {:.2f}) to {} (curr. prob. {:.2f}) to gain {}".format(
                        node, current_community, old_val[current_community], new_community, old_val[new_community], diff.item()))
                    node_max_gain[node] = max(node_max_gain[node], diff.item())
            if node_max_gain[node] > 0:
                moveable_nonbin += 1
        else:
            diffs = Q2[node, :] @ (C - C[:, [current_community]])
            new_community = diffs.max(0).indices.item()
            node_max_gain[node] = diffs[new_community].item()
            if verbosity > 1 and node_max_gain[node] > 0:
                print("move node {} from {} to {} to gain {}".format(node, current_community, new_community, node_max_gain[node]))
    ratio_nonbin = "{} non-binary out of {}, {} moveable".format(non_bin, C.shape[1], moveable_nonbin)
    return ratio_nonbin, "{} nodes could be moved with total gain {}".format(sum(node_max_gain > 0), node_max_gain.sum())

def test_move_gains():
    Q = [[1, 2, -1],
        [2, 5, 1],
        [-1,1, 10]]
    Q = torch.FloatTensor(Q)
    C = [[0.3, 0.3, 0.4],
        [1, 0, 0],
        [0, 0, 1]]
    C = torch.FloatTensor(C)
    print(move_gains(C, Q))
    print("try simple:")
    move_gains_old_slow_reliable_version(C, Q)

#test_move_gains()

In [6]:
def perturb(A):
    p = 0.4
    #epsilon = torch.rand(A.shape).uniform_(0, p) - torch.rand(A.shape).uniform_(0, p)
    #return torch.clip(A + epsilon,0,1)
    epsilon = p * torch.rand(A.shape)
    C = A + epsilon
    return C / C.sum(dim=-1, keepdim=True)

In [7]:
def spectralPartition(A, nb_comm):
    clustering = SpectralClustering(n_clusters=nb_comm,assign_labels='discretize',random_state=0).fit(A)
    clusters = list(clustering.labels_)
    partitions = torch.tensor(clusters)
    return torch.nn.functional.one_hot(partitions)

In [8]:
def test_spectral():
    G = nx.Graph()
    G.add_nodes_from(range(8))
    G.add_edges_from([(0, 1), (1, 2), (2, 3), (3, 4), (4, 5), (5, 6), (6, 7),
        (2, 5)])
    print(nx.linalg.algebraicconnectivity.fiedler_vector(G))

def test_spectral2():
    Gs = [(nx.karate_club_graph(), 'karate')]
    net_names = ["David Copperfield","Jazz Musicians","Dolphins Social Network"]
    for net_name in net_names:
        Gs.append((nx.read_pajek('../data/'+net_name+'.net').to_undirected(), net_name))
    for G, net_name in Gs:
        A = torch.FloatTensor(nx.to_numpy_array(G))
        p = spectralPartition(A, 4)
        Q = modularity_matrix(A)
        #print(p.argmax(dim=1))
        print()
        print(-modularity(p.float(), Q))
        clusters = SpectralClustering(n_clusters=4,affinity='precomputed',assign_labels='discretize',random_state=0).fit_predict(A)
        partitions = torch.tensor(clusters)
        #print(clusters)
        print(-modularity(torch.nn.functional.one_hot(partitions).float(), Q))
        clusters2 = SpectralClustering(n_clusters=4,affinity='precomputed',random_state=0).fit_predict(A)
        partitions2 = torch.LongTensor(clusters)
        #print(clusters)
        print(-modularity(torch.nn.functional.one_hot(partitions).float(), Q))

#test_spectral2()

In [9]:
def test_embed():
    adj = torch.tensor([
        [0, 1.0, 0, 1],
        [1, 0, 1, 0],
        [0, 1, 0, 1],
        [1, 0, 1, 0],
    ])
    U, S, Vh = torch.linalg.svd(adj)
    print(S, S.shape)
    dim = 2
    mu = torch.matmul(torch.matmul(U[:, :dim], torch.diag(S[:dim])), Vh[:dim, :])
    print(mu)
    embedx = U[:, :dim] * torch.pow(S[:dim], 0.5)
    print(embedx)
    embedy = torch.pow(S[:dim], 0.5) * Vh[:dim, :].T
    print(embedy)
    print(embedx @ embedy.T)
    embed = torch.cat((embedx, embedy), axis=-1)
    print(embed)
    print(embed @ embed.T)

#test_embed()

In [10]:
def svdApprox(adj, dim, relu=False):
    U, S, Vh = torch.linalg.svd(adj)
    mu = torch.matmul(torch.matmul(U[:, :dim], torch.diag(S[:dim])), Vh[:dim, :])

    embedx = torch.matmul(U[:, :dim], torch.diag(torch.pow(S[:dim], 0.5)))
    embedy = torch.transpose(torch.matmul(torch.diag(torch.pow(S[:dim], 0.5)), Vh[:dim, :]), 0, 1)

    criterion = torch.nn.GaussianNLLLoss()
    if relu:
        crt = torch.nn.ReLU()
        mu = crt(mu)
    mse = torch.nn.MSELoss()
    mseloss = mse(torch.flatten(mu), torch.flatten(adj))
    sig = torch.sqrt(mseloss)
    sigma = sig * torch.ones(adj.shape)
    loss = criterion(torch.flatten(adj), torch.flatten(mu), torch.flatten(torch.square(sigma)))

    return embedx, embedy

# Features

In [32]:
def get_features_orig(G, method, seed=None):
    mod_before_perturb = -1
    adj = nx.to_numpy_array(G)
    adj = torch.FloatTensor(adj)
    Q = modularity_matrix(adj)
    #Combo
    combo_partition, combo_mod = pycombo.execute(G, random_seed=seed)
    nb_comm = max(combo_partition.values())+1
    if method == "combo":
        communities =  np.array(list(combo_partition.values())).reshape(-1)
        orig_partition = np.eye(nb_comm)[communities]
        features = torch.FloatTensor(orig_partition)
        mod_before_perturb = -modularity(features, Q)
        assert abs(mod_before_perturb.item() - combo_mod) < 1e-6, (mod_before_perturb.item(), combo_mod)
    elif method == "louvain":
        partition = community_louvain.best_partition(G)
        #get binary matrix of the partition
        nb_community = max(list(partition.values())) + 1
        communities =  np.array(list(partition.values())).reshape(-1)
        orig_partition = np.eye(nb_community)[communities]
        features = torch.FloatTensor(orig_partition)
        mod_before_perturb = -modularity(features, Q)
        features = perturb(features)
    elif method == "spectral":
        features = spectralPartition(adj, nb_comm).float()
        mod_before_perturb = -modularity(features, Q)
    else:
        if seed:
            np.random.seed(seed)
        communities =  np.random.random_integers(0, nb_comm - 1, len(G))
        orig_partition = np.eye(nb_comm)[communities]
        features = torch.FloatTensor(orig_partition)
        mod_before_perturb = -modularity(features, Q)
    return features, adj, Q, mod_before_perturb, combo_mod

def get_features(G):
    mod_before_perturb = -1
    adj = nx.to_numpy_array(G)
    adj = np.expand_dims(adj, axis=0)
    Q = torch.FloatTensor(adj)
    #Combo
    combo_partition, combo_mod = pycombo.execute(G, treat_as_modularity=True, random_seed=seed)
    orig_partition = np.array([[0,0,1],[0,0,1],[1,0,0],[1,0,0],[1,0,0],[1,0,0]])
    #orig_partition = np.array([[0.9,0,0.1],[0.9,0.1,0],[1,0,0]])
    features = torch.FloatTensor(orig_partition)
    mod_before_perturb = -modularity(features, Q)
    return features, adj, Q, mod_before_perturb, combo_mod

# Models

## GNNS

In [24]:
def GNNS(model_name, G, features, adj, Q, optimizer_class, n_epochs=1000, lr=0.002, seed=None, verbosity=2):
    if seed:
        np.random.seed(seed)
        torch.manual_seed(seed)
    t_total = time.time()
    adj_norm = normalize(adj)
    Q_norm = Q / abs(Q).sum(dim=1, keepdim=True) #not needed as using Q gives the same result
    C = features
    init_mod = torch.trace(C.T @ Q @ C)
    f0 = -0.5
    f1 = 0.5
    f2 = 1.0
    for epoch in range(n_epochs):
        t_1run = time.time()
        t = (Q @ C).max(dim=1, keepdim=True).values
        C = f0 + f1 * C + f2 * (Q @ C) / t
        #normalize
        #C = F.relu(C) #replaced to be comparable with GNN
        C = 1.0 + C - C.max(dim=-1, keepdim=True).values
        C = torch.clamp(C, 0, 1)
        C = C / C.sum(dim=-1, keepdim=True) #normalize st sum = 1
        #loss
        Q1 = torch.mm(C.T, Q)
        Q2 = torch.mm(Q1, C)
        loss = torch.trace(Q2)
        loss = -loss
        if epoch == 0:
            best_loss = loss
            best_C = C.data
        else:
            if loss < best_loss:
                best_loss = loss
                best_C = C.data
                best_epoch = epoch
        if verbosity > 1 and (n_epochs <= 20 or epoch % (n_epochs//20) == 0 or epoch == n_epochs - 1):
            print('Epoch: {:04d}'.format(epoch + 1),
                  #'Modularity: {:.8f}'.format(-best_loss.item()),
                  'Modularity: {:.8f}'.format(-loss.item()),
                  'time: {:.4f}s'.format(time.time() - t_1run))
    #t = (Q @ best_C).max(dim=1, keepdim=True).values
    #best_C = f0 + f1 * best_C + f2 * (Q @ best_C) / t
    #best_loss = torch.trace(best_C.T @ Q @ best_C)
    best_loss = -best_loss
    if verbosity > 0:
        print("Optimization Finished!")
        print("Total time elapsed: {:.4f}s".format(time.time() - t_total))
    ratio_nonbin, node_max_gain = move_gains(best_C, Q, verbosity)
    return init_mod, best_loss, best_C, ratio_nonbin, node_max_gain

## Simple community label optimization

In [15]:
class GNN_simplest(nn.Module):
    def __init__(self, features):
        super(GNN_simplest, self).__init__()
        self.C = nn.Parameter(features)

    def forward(self):
        newC = self.C
        #newC = newC / newC.sum(dim=-1, keepdim=True) #normalize st sum = 1
        newC = 1.0 + newC - newC.max(dim=-1, keepdim=True).values
        newC = torch.clamp(newC, 0, 1)
        #newC = F.relu(newC)
        newC = newC / newC.sum(dim=-1, keepdim=True) #normalize st sum = 1
        return newC

## GNN

In [68]:
class GNNLayer(nn.Module):
    def __init__(self, in_features, out_features, dropout=0.0):
        super(GNNLayer, self).__init__()
        self.weight1 = nn.Parameter(0.5 * torch.eye(in_features, out_features))
        #self.weight2 = nn.Parameter(torch.zeros(in_features, out_features))
        self.weight2 = nn.Parameter(1.0 * torch.eye(in_features, out_features))
        self.bias = nn.Parameter(-0.5 * torch.ones(1, out_features))
        self.dropout = dropout

    def forward(self, input, adj):
        v1 = torch.mm(input, self.weight1)
        v2 = torch.mm(adj, input)
        #v2 = v2 / (v2.max(dim=1, keepdim=True).values + 1e-9)
        v2 = torch.mm(v2, self.weight2)
        output = v1 + v2 + self.bias
        output = F.dropout(output, p=self.dropout, training=self.training)
        return output

class GNNLayerDiag(nn.Module):
    def __init__(self, n_features, dropout=0.0):
        super(GNNLayerDiag, self).__init__()
        self.weight1 = nn.Parameter(0.5 * torch.ones(1, n_features))
        self.weight2 = nn.Parameter(1.0 * torch.ones(1, n_features))
        self.bias = nn.Parameter(-0.5 * torch.ones(1, n_features))
        #self.weight1 = nn.Parameter(1.0 * torch.ones(1, n_features))
        #self.weight2 = nn.Parameter(torch.zeros(1, n_features))
        #self.bias = nn.Parameter(-1.0 * torch.zeros(1, n_features))
        self.dropout = dropout

    def forward(self, input, adj):
        v1 = self.weight1 * input
        v2 = torch.mm(adj, input)
        #v2 = v2 / (v2.max(dim=1, keepdim=True).values + 1e-9)
        v2 = self.weight2 * v2
        output = v1 + v2 + self.bias
        output = F.dropout(output, p=self.dropout, training=self.training)
        return output

class GNN_1L(nn.Module):
    def __init__(self, in_features, out_features, diag=False, dropout=0.0):
        super(GNN_1L, self).__init__()
        if diag:
            self.gc1 = GNNLayerDiag(in_features, dropout)
        else:
            self.gc1 = GNNLayer(in_features, out_features, dropout)

    def forward(self, x, adj):
        x = self.gc1(x, adj)
        #x = nn.Softmax(dim=2)(x)
        x = 1.0 + x - x.max(dim=-1, keepdim=True).values
        x = torch.clamp(x, 0, 1)
        x = x / x.sum(dim=-1, keepdim=True) #normalize st sum = 1
        return x

class GNN_2L(nn.Module):
    def __init__(self, in_features, hidden, out_features):
        super(GNN_2L, self).__init__()
        self.gc1 = GNNLayer(in_features, hidden)
        self.gc2 = GNNLayer(hidden, out_features)

    def forward(self, x, adj):
        x = self.gc1(x, adj)
        x = torch.clamp(x, 0, 1)
        x = self.gc2(x, adj)
        x = torch.clamp(x, 0, 1)
        x = x / x.sum(dim=-1, keepdim=True) #normalize st sum = 1
        return x


In [64]:
class GAttentionHead(torch.nn.Module):
    def __init__(self, in_features, out_features):
        super().__init__()
        #self.W1 = nn.Parameter(torch.empty(size=(in_features, out_features))) # F X F'
        #nn.init.xavier_uniform_(self.W1.data, gain=1.414)
        self.W1 = nn.Parameter(0.5 * torch.eye(in_features, out_features))
        #self.W2 = nn.Parameter(torch.empty(size=(in_features, out_features))) # F X F'
        #nn.init.xavier_uniform_(self.W2.data, gain=1.414)
        self.W2 = nn.Parameter(1.0 * torch.eye(in_features, out_features))
        #self.bias = nn.Parameter(torch.zeros(size=(1, out_features))) # 1 X F'
        self.bias = nn.Parameter(-0.5 * torch.ones(1, out_features))
        self.a = nn.Parameter(torch.empty(size=(2*out_features, 1))) # 2F' X 1
        nn.init.xavier_uniform_(self.a.data, gain=1.414)
        self.k1 = 1.0#nn.Parameter(torch.scalar_tensor(1.0))
        self.k2 = 0.0#nn.Parameter(torch.scalar_tensor(1e-9))
        self.leaky_relu = nn.LeakyReLU(0.2)
    
    def forward(self, fts, Q):
        #new_fts = fts
        new_fts = torch.mm(fts, self.W2)
        edges = (Q > 0).nonzero(as_tuple=True) # ([u1, u2, ...], [v1, v2, ....])
        a_input = torch.cat([new_fts[edges[0]], new_fts[edges[1]]], dim=1) # |E| x 2F'
        e = self.leaky_relu(torch.mm(a_input, self.a).squeeze())
        e_full = torch.full_like(Q, -9e15)
        e_full[edges] = e
        alphas = F.softmax(e_full, dim=1)
        w = self.k1 * Q + self.k2 * alphas
        v1 = torch.mm(fts, self.W1)
        v2 = torch.mm(w, new_fts)
        #v2 = v2 / (v2.max(dim=1, keepdim=True).values + 1e-9)
        #v2 = torch.mm(v2, self.W2)
        ret_fts = v2 + v1 + self.bias
        return ret_fts

class GATLayer(torch.nn.Module):
    def __init__(self, num_heads, in_features, out_features):
        super().__init__()
        heads = []
        for _ in range(num_heads):
            heads.append(GAttentionHead(in_features, out_features))
        self.heads = nn.ModuleList(heads)

    def forward(self, fts, adj):
        outs = [head(fts, adj) for head in self.heads]
        return torch.mean(torch.stack(outs), dim=0)

class GNN_1Attention(torch.nn.Module):
    def __init__(self, in_features, out_features, num_heads=1):
        super().__init__()
        self.gat1 = GATLayer(num_heads, in_features, out_features)
    
    def forward(self, x, adj):
        x = self.gat1(x, adj)
        x = 1.0 + x - x.max(dim=-1, keepdim=True).values
        x = torch.clamp(x, 0, 1)
        x = x / x.sum(dim=-1, keepdim=True) #normalize st sum = 1
        return x

# Training

In [56]:
def train(model_name, G, features, embed_size, adj, Q, optimizer_class, n_epochs=1000, lr=0.002, seed=None, verbosity=2):
    if seed:
        np.random.seed(seed)
        torch.manual_seed(seed)
    t_total = time.time()
    n_comm = features.shape[-1] - embed_size
    adj_norm = normalize(adj)
    Q_norm = Q / abs(Q).sum(dim=1, keepdim=True)
    init_mod = torch.trace(features.T @ Q @ features)
    if model_name[:2] == '1L':
        model = GNN_1L(features.shape[1], n_comm)
    elif model_name[:2] == '1D':
        model = GNN_1L(features.shape[1], n_comm, diag=True)
    elif model_name[:2] == '1A':
        model = GNN_1Attention(features.shape[1], n_comm)
    elif model_name[:2] == '2L':
        model = GNN_2L(features.shape[1], features.shape[1] + 3, n_comm)
    elif model_name == 'simple':
        model = GNN_simplest(features)
    else:
        assert False, 'unexpected model_name'
    optimizer = optimizer_class(model.parameters(), lr=lr)
    for epoch in range(n_epochs):
        t_1run = time.time()
        optimizer.zero_grad()
        if model_name[2] == 'q':
            out_embed = model(features, Q_norm)
        elif model_name[2] == 'a':
            out_embed = model(features, adj_norm)
        elif model_name[2] == 't':
            out_embed = model(features, Q_norm)
        elif model_name == 'simple':
            out_embed = model()
        else:
            assert False, 'unexpected model_name'
        C = out_embed#[:, :n_comm]
        Q1 = torch.mm(C.T, Q)
        Q2 = torch.mm(Q1, C)
        loss = torch.trace(Q2)
        loss = -loss
        loss.backward()
        optimizer.step()
        if epoch == 0:
            best_loss = loss
            best_C = C.data
            best_embed = out_embed.data
        else:
            if loss < best_loss:
                best_loss = loss
                best_C = C.data
                best_embed = out_embed.data
                best_epoch = epoch
        if n_epochs <= 20 or epoch % (n_epochs//20) == 0 or epoch == n_epochs - 1:
            print('Epoch: {:04d}'.format(epoch + 1),
                  'Modularity: {:.8f}'.format(-best_loss.item()),
                  'time: {:.4f}s'.format(time.time() - t_1run))
    print("Optimization Finished!")
    print("Total time elapsed: {:.4f}s".format(time.time() - t_total))
    ratio_nonbin, node_max_gain = move_gains(best_C, Q)
    return init_mod, -best_loss, best_embed, ratio_nonbin, node_max_gain

def run_experiment(model_name, network, optimizer_class=optim.SGD, n_epochs=1000, partition_method='spectral',
                    init_features=None, embed_dim=0, seed=None, verbosity=2):
    print("->>starting {} optimization using {}".format(model_name, optimizer_class))
    #network = nx.Graph()
    #network.add_nodes_from(range(6))
    #network.add_edges_from([(0, 1, {'weight': 1.0}), (0, 2, {'weight': -10}), (0, 3, {'weight': 1}), (0, 4, {'weight': -10}), (0, 5, {'weight': -10}),
    #                    (1, 2, {'weight': 1.2}), (1, 3, {'weight': -10}), (1, 4, {'weight': -10}), (1, 5, {'weight': -10}),
    #                    (2, 3, {'weight': 1}), (2, 4, {'weight': -1}), (2, 5, {'weight': 0.5}),
    #                    (3, 4, {'weight': 0.5}), (3, 5, {'weight': -1})])
    features, adj, Q, mod_before_perturb, combo_mod = get_features_orig(network, partition_method, seed=seed)
    if init_features is None:
        print("Combo's modularity = {:.8f}, modularity before perturbation = {:.8f}".format(combo_mod, mod_before_perturb.item()))
        init_features = features
    if model_name == 'GNNS':
        init_mod, finetuned_mod, features, ratio_nonbin, node_max_gain = GNNS(model_name, network, init_features, adj, Q, optimizer_class, n_epochs, seed=seed, verbosity=verbosity)
    else:
        embedx, embedy = svdApprox(adj, dim=embed_dim)
        init_features = torch.cat((init_features, embedx, embedy),axis=-1)
        init_mod, finetuned_mod, features, ratio_nonbin, node_max_gain = train(model_name, network, init_features, embed_dim * 2, adj, Q, optimizer_class, n_epochs, seed=seed, verbosity=verbosity)
    if verbosity > 0:
        print("Starting from init. modularity = {}, achieved modularity = {}".format(init_mod, finetuned_mod))
    return features, finetuned_mod, combo_mod

In [40]:
def random_trials(model_name, embed_dim=0, num_tries=5):
    t_total = time.time()
    net_names=["karate", "David Copperfield","Jazz Musicians","Dolphins Social Network"]
    results = {'Method': '{} with {} random starts'.format(model_name, num_tries)}
    for net_name in net_names:
        print("\t\tStarting processing net {}".format(net_name))
        if net_name == 'karate':
            network = nx.karate_club_graph()
        else:
            network = nx.read_pajek('../data/'+net_name+'.net').to_undirected()

        best_mod = -1
        best_res = []
        for i in range(num_tries):
            print("\t->>Starting trial ", i)
            new_features, new_mod, combo_mod = run_experiment(model_name, network, optim.Adam, n_epochs=2000, partition_method='rand', embed_dim=embed_dim, seed=7*i)
            old_mod = -1
            while new_mod > old_mod:
                old_mod = new_mod
                new_features, new_mod, _ = run_experiment(model_name, network, optim.SGD, n_epochs=1000, init_features=new_features)
            print("starting Adam")
            old_mod = -1
            while new_mod > old_mod:
                old_mod = new_mod
                new_features, new_mod, _ = run_experiment(model_name, network, optim.Adam, n_epochs=1000, init_features=new_features)
            if best_mod < new_mod:
                best_mod = new_mod
                best_res = new_features
        print("Best mod for net {} is {}\n\n\n".format(net_name, best_mod))
        results[net_name] = best_mod.item()
    results['time'] = time.time() - t_total
    return results

# Seed params

In [22]:
temp_seed = 17
embed_dim = 2

# GNNS

In [25]:
network = get_network("Dolphins Social Network")
new_features, new_mod, combo_mod = run_experiment('GNNS', network, n_epochs=200, partition_method='rand', seed=temp_seed)

->>starting GNNS optimization using <class 'torch.optim.sgd.SGD'>
Combo's modularity = 0.52679878, modularity before perturbation = -0.04902892
Epoch: 0001 Modularity: 0.07054657 time: 0.0002s
Epoch: 0011 Modularity: 0.52126241 time: 0.0002s
Epoch: 0021 Modularity: 0.52123231 time: 0.0001s
Epoch: 0031 Modularity: 0.52123231 time: 0.0003s
Epoch: 0041 Modularity: 0.52123231 time: 0.0001s
Epoch: 0051 Modularity: 0.52123231 time: 0.0001s
Epoch: 0061 Modularity: 0.52123231 time: 0.0001s
Epoch: 0071 Modularity: 0.52123231 time: 0.0001s
Epoch: 0081 Modularity: 0.52123231 time: 0.0001s
Epoch: 0091 Modularity: 0.52123231 time: 0.0001s
Epoch: 0101 Modularity: 0.52123231 time: 0.0001s
Epoch: 0111 Modularity: 0.52123231 time: 0.0001s
Epoch: 0121 Modularity: 0.52123231 time: 0.0001s
Epoch: 0131 Modularity: 0.52123231 time: 0.0001s
Epoch: 0141 Modularity: 0.52123231 time: 0.0001s
Epoch: 0151 Modularity: 0.52123231 time: 0.0001s
Epoch: 0161 Modularity: 0.52123231 time: 0.0001s
Epoch: 0171 Modularity:

In [26]:
def random_trials_GNNS(num_tries=5):
    t_total = time.time()
    net_names=["karate", "David Copperfield","Jazz Musicians","Dolphins Social Network"]
    results = {'Method': '{} with {} random starts'.format('GNNS', num_tries)}
    results_combo = {'Method': 'Combo'}
    for net_name in net_names:
        print("\t\tStarting processing net {}".format(net_name))
        if net_name == 'karate':
            network = nx.karate_club_graph()
        else:
            network = nx.read_pajek('../data/'+net_name+'.net').to_undirected()
        best_mod = -1
        best_res = []
        for i in range(num_tries):
            print("\t->>Starting trial ", i)
            new_features, new_mod, combo_mod = run_experiment('GNNS', network, n_epochs=20, partition_method='rand', seed=7*i)
            old_mod = -1
            while new_mod > old_mod:
                old_mod = new_mod
                new_features, new_mod, _ = run_experiment('GNNS', network, n_epochs=10, init_features=new_features)
            if best_mod < new_mod:
                best_mod = new_mod
                best_res = new_features
        print("Best mod for net {} is {}\n\n\n".format(net_name, best_mod))
        results[net_name] = best_mod.item()
        results_combo[net_name] = combo_mod
    results['time'] = time.time() - t_total
    results_combo['time'] = -1
    return results, results_combo

results_GNNS, results_combo = random_trials_GNNS()

		Starting processing net karate
	->>Starting trial  0
->>starting GNNS optimization using <class 'torch.optim.sgd.SGD'>
Combo's modularity = 0.41978961, modularity before perturbation = 0.00788955
Epoch: 0001 Modularity: 0.12092515 time: 0.0002s
Epoch: 0002 Modularity: 0.21375078 time: 0.0008s
Epoch: 0003 Modularity: 0.23108360 time: 0.0006s
Epoch: 0004 Modularity: 0.25097296 time: 0.0004s
Epoch: 0005 Modularity: 0.25816563 time: 0.0004s
Epoch: 0006 Modularity: 0.26892316 time: 0.0005s
Epoch: 0007 Modularity: 0.28635782 time: 0.0004s
Epoch: 0008 Modularity: 0.32044291 time: 0.0004s
Epoch: 0009 Modularity: 0.35622895 time: 0.0003s
Epoch: 0010 Modularity: 0.38926792 time: 0.0004s
Epoch: 0011 Modularity: 0.39222655 time: 0.0004s
Epoch: 0012 Modularity: 0.39161524 time: 0.0003s
Epoch: 0013 Modularity: 0.39230451 time: 0.0007s
Epoch: 0014 Modularity: 0.39172906 time: 0.0017s
Epoch: 0015 Modularity: 0.39232707 time: 0.0011s
Epoch: 0016 Modularity: 0.39176574 time: 0.0006s
Epoch: 0017 Modula

# Simple

## One network tests

### karate

In [20]:
network = get_network("karate")
new_features, new_mod, combo_mod = run_experiment('simple', network, optim.Adam, n_epochs=2000, partition_method='spectral')

->>starting simple optimization using <class 'torch.optim.adam.Adam'>
Combo's modularity = 0.41978961, modularity before perturbation = 0.34015453
Epoch: 0001 Modularity: 0.34015453 time: 0.0007s
Epoch: 0101 Modularity: 0.35850057 time: 0.0008s
Epoch: 0201 Modularity: 0.36416149 time: 0.0004s
Epoch: 0301 Modularity: 0.36829615 time: 0.0002s
Epoch: 0401 Modularity: 0.37089938 time: 0.0006s
Epoch: 0501 Modularity: 0.37278268 time: 0.0003s
Epoch: 0601 Modularity: 0.37522066 time: 0.0002s
Epoch: 0701 Modularity: 0.38014346 time: 0.0002s
Epoch: 0801 Modularity: 0.39196938 time: 0.0002s
Epoch: 0901 Modularity: 0.40203816 time: 0.0002s
Epoch: 1001 Modularity: 0.40203816 time: 0.0002s
Epoch: 1101 Modularity: 0.40203816 time: 0.0002s
Epoch: 1201 Modularity: 0.40203816 time: 0.0002s
Epoch: 1301 Modularity: 0.40203816 time: 0.0002s
Epoch: 1401 Modularity: 0.40203816 time: 0.0002s
Epoch: 1501 Modularity: 0.40203816 time: 0.0002s
Epoch: 1601 Modularity: 0.40203816 time: 0.0002s
Epoch: 1701 Modulari

In [21]:
new_features, new_mod, combo_mod = run_experiment('simple', network, optim.Adam, n_epochs=2000, partition_method='spectral')
old_mod = -1
while new_mod > old_mod:
    old_mod = new_mod
    new_features, new_mod, _ = run_experiment('simple', network, optim.SGD, n_epochs=1000, init_features=new_features)
print("starting Adam")
old_mod = -1
while new_mod > old_mod:
    old_mod = new_mod
    new_features, new_mod, _ = run_experiment('simple', network, optim.Adam, n_epochs=1000, init_features=new_features)

->>starting simple optimization using <class 'torch.optim.adam.Adam'>
Combo's modularity = 0.41978961, modularity before perturbation = 0.34015453
Epoch: 0001 Modularity: 0.34015453 time: 0.0004s
Epoch: 0101 Modularity: 0.35850057 time: 0.0002s
Epoch: 0201 Modularity: 0.36416149 time: 0.0002s
Epoch: 0301 Modularity: 0.36829615 time: 0.0002s
Epoch: 0401 Modularity: 0.37089938 time: 0.0002s
Epoch: 0501 Modularity: 0.37278268 time: 0.0002s
Epoch: 0601 Modularity: 0.37522066 time: 0.0002s
Epoch: 0701 Modularity: 0.38014346 time: 0.0002s
Epoch: 0801 Modularity: 0.39196938 time: 0.0002s
Epoch: 0901 Modularity: 0.40203816 time: 0.0002s
Epoch: 1001 Modularity: 0.40203816 time: 0.0002s
Epoch: 1101 Modularity: 0.40203816 time: 0.0002s
Epoch: 1201 Modularity: 0.40203816 time: 0.0002s
Epoch: 1301 Modularity: 0.40203816 time: 0.0002s
Epoch: 1401 Modularity: 0.40203816 time: 0.0002s
Epoch: 1501 Modularity: 0.40203816 time: 0.0002s
Epoch: 1601 Modularity: 0.40203816 time: 0.0002s
Epoch: 1701 Modulari

### Dolphins

In [22]:
network = get_network("Dolphins Social Network")
new_features, new_mod, combo_mod = run_experiment('simple', network, optim.Adam, n_epochs=2000, partition_method='spectral')
if False:
    old_mod = -1
    while new_mod > old_mod:
        old_mod = new_mod
        new_features, new_mod, _ = run_experiment('simple', network, optim.SGD, n_epochs=1000, init_features=new_features)
    print("starting Adam")
    old_mod = -1
    while new_mod > old_mod:
        old_mod = new_mod
        new_features, new_mod, _ = run_experiment('simple', network, optim.Adam, n_epochs=1000, init_features=new_features)

->>starting simple optimization using <class 'torch.optim.adam.Adam'>
Combo's modularity = 0.52679878, modularity before perturbation = 0.26804712
Epoch: 0001 Modularity: 0.26804712 time: 0.0005s
Epoch: 0101 Modularity: 0.30891666 time: 0.0002s
Epoch: 0201 Modularity: 0.32189605 time: 0.0002s
Epoch: 0301 Modularity: 0.32952338 time: 0.0002s
Epoch: 0401 Modularity: 0.33626285 time: 0.0002s
Epoch: 0501 Modularity: 0.34850144 time: 0.0002s
Epoch: 0601 Modularity: 0.35663867 time: 0.0002s
Epoch: 0701 Modularity: 0.37097794 time: 0.0002s
Epoch: 0801 Modularity: 0.39839122 time: 0.0002s
Epoch: 0901 Modularity: 0.42351586 time: 0.0002s
Epoch: 1001 Modularity: 0.42709854 time: 0.0002s
Epoch: 1101 Modularity: 0.42779452 time: 0.0002s
Epoch: 1201 Modularity: 0.42796946 time: 0.0002s
Epoch: 1301 Modularity: 0.42828235 time: 0.0002s
Epoch: 1401 Modularity: 0.42870355 time: 0.0002s
Epoch: 1501 Modularity: 0.42871270 time: 0.0002s
Epoch: 1601 Modularity: 0.42872116 time: 0.0002s
Epoch: 1701 Modulari

## Random tries

In [41]:
results_simple = random_trials('simple')

		Starting processing net karate
	->>Starting trial  0
->>starting simple optimization using <class 'torch.optim.adam.Adam'>
Combo's modularity = 0.41978961, modularity before perturbation = -0.05728139
Epoch: 0001 Modularity: -0.05728139 time: 0.0007s
Epoch: 0101 Modularity: 0.04344017 time: 0.0002s
Epoch: 0201 Modularity: 0.08304624 time: 0.0002s
Epoch: 0301 Modularity: 0.10831866 time: 0.0002s
Epoch: 0401 Modularity: 0.12574606 time: 0.0002s
Epoch: 0501 Modularity: 0.14403452 time: 0.0002s
Epoch: 0601 Modularity: 0.18510455 time: 0.0002s
Epoch: 0701 Modularity: 0.24153039 time: 0.0002s
Epoch: 0801 Modularity: 0.27550924 time: 0.0002s
Epoch: 0901 Modularity: 0.29317772 time: 0.0002s
Epoch: 1000 Modularity: 0.30781743 time: 0.0002s
Epoch: 1001 Modularity: 0.30786887 time: 0.0007s
Epoch: 1101 Modularity: 0.30892506 time: 0.0002s
Epoch: 1201 Modularity: 0.30892506 time: 0.0002s
Epoch: 1301 Modularity: 0.30892506 time: 0.0002s
Epoch: 1401 Modularity: 0.30892506 time: 0.0002s
Epoch: 1501 

In [31]:
results_simple

{'Method': 'simple with 5 random starts',
 'karate': tensor(0.4198, grad_fn=<NegBackward0>),
 'David Copperfield': tensor(0.3011, grad_fn=<NegBackward0>),
 'Jazz Musicians': tensor(0.4443, grad_fn=<NegBackward0>),
 'Dolphins Social Network': tensor(0.5268, grad_fn=<NegBackward0>)}

# 1-Layer GAT

## One network tests

### Dolphins

In [71]:
network = get_network("Dolphins Social Network")
new_features, new_mod, combo_mod = run_experiment('1Lq', network, optim.Adam, n_epochs=20000, partition_method='rand', embed_dim=embed_dim, seed=temp_seed)

->>starting 1Lq optimization using <class 'torch.optim.adam.Adam'>
Combo's modularity = 0.52679878, modularity before perturbation = -0.04902892
Epoch: 0001 Modularity: 0.01258716 time: 0.0017s
Epoch: 1001 Modularity: 0.42087609 time: 0.0003s
Epoch: 2001 Modularity: 0.43360966 time: 0.0003s
Epoch: 3001 Modularity: 0.44623610 time: 0.0003s
Epoch: 4001 Modularity: 0.44723913 time: 0.0004s
Epoch: 5001 Modularity: 0.44747388 time: 0.0003s
Epoch: 6001 Modularity: 0.44748655 time: 0.0007s
Epoch: 7001 Modularity: 0.44749478 time: 0.0003s
Epoch: 8001 Modularity: 0.44750139 time: 0.0003s
Epoch: 9001 Modularity: 0.44750369 time: 0.0003s
Epoch: 10001 Modularity: 0.44750524 time: 0.0003s
Epoch: 11001 Modularity: 0.44750610 time: 0.0003s
Epoch: 12001 Modularity: 0.44750676 time: 0.0003s
Epoch: 13001 Modularity: 0.44750682 time: 0.0003s
Epoch: 14001 Modularity: 0.44750682 time: 0.0003s
Epoch: 15001 Modularity: 0.44750684 time: 0.0003s
Epoch: 16001 Modularity: 0.44750684 time: 0.0003s
Epoch: 17001 Mo

In [72]:
network = get_network("Dolphins Social Network")
new_features, new_mod, combo_mod = run_experiment('1At', network, optim.Adam, n_epochs=20000, partition_method='rand', embed_dim=embed_dim, seed=temp_seed)

->>starting 1At optimization using <class 'torch.optim.adam.Adam'>
Combo's modularity = 0.52679878, modularity before perturbation = -0.04902892
Epoch: 0001 Modularity: 0.01258716 time: 0.0024s
Epoch: 1001 Modularity: 0.42085776 time: 0.0007s
Epoch: 2001 Modularity: 0.43356457 time: 0.0007s
Epoch: 3001 Modularity: 0.44633120 time: 0.0005s
Epoch: 4001 Modularity: 0.44776252 time: 0.0007s
Epoch: 5001 Modularity: 0.44860321 time: 0.0006s
Epoch: 6001 Modularity: 0.44958949 time: 0.0005s
Epoch: 7001 Modularity: 0.45336640 time: 0.0005s
Epoch: 8001 Modularity: 0.45815429 time: 0.0005s
Epoch: 9001 Modularity: 0.45888212 time: 0.0005s
Epoch: 10001 Modularity: 0.45888212 time: 0.0005s
Epoch: 11001 Modularity: 0.45888212 time: 0.0005s
Epoch: 12001 Modularity: 0.45888212 time: 0.0005s
Epoch: 13001 Modularity: 0.45888212 time: 0.0006s
Epoch: 14001 Modularity: 0.45888212 time: 0.0005s
Epoch: 15001 Modularity: 0.45888212 time: 0.0005s
Epoch: 16001 Modularity: 0.45888212 time: 0.0005s
Epoch: 17001 Mo

In [29]:
network = get_network("Dolphins Social Network")
new_features, new_mod, combo_mod = run_experiment('1At', network, optim.Adam, n_epochs=10000, partition_method='rand', embed_dim=embed_dim, seed=temp_seed)

->>starting 1At optimization using <class 'torch.optim.adam.Adam'>
Combo's modularity = 0.52679878, modularity before perturbation = -0.04902892
Epoch: 0001 Modularity: 0.00504321 time: 0.0008s
Epoch: 0501 Modularity: 0.42529052 time: 0.0005s
Epoch: 1001 Modularity: 0.44435659 time: 0.0005s
Epoch: 1501 Modularity: 0.44741103 time: 0.0005s
Epoch: 2001 Modularity: 0.44741103 time: 0.0005s
Epoch: 2501 Modularity: 0.44741103 time: 0.0005s
Epoch: 3001 Modularity: 0.44741103 time: 0.0006s
Epoch: 3501 Modularity: 0.44741103 time: 0.0006s
Epoch: 4001 Modularity: 0.44741103 time: 0.0005s
Epoch: 4501 Modularity: 0.44741103 time: 0.0005s
Epoch: 5001 Modularity: 0.44741103 time: 0.0005s
Epoch: 5501 Modularity: 0.44741103 time: 0.0005s
Epoch: 6001 Modularity: 0.44741103 time: 0.0005s
Epoch: 6501 Modularity: 0.44741103 time: 0.0005s
Epoch: 7001 Modularity: 0.44741103 time: 0.0006s
Epoch: 7501 Modularity: 0.44741103 time: 0.0005s
Epoch: 8001 Modularity: 0.44741103 time: 0.0005s
Epoch: 8501 Modularity

In [25]:
old_mod = -1
while new_mod > old_mod:
    old_mod = new_mod
    new_features, new_mod, _ = run_experiment('1At', network, optim.Adam, n_epochs=1000, init_features=new_features, embed_dim=embed_dim)

->>starting 1At optimization using <class 'torch.optim.adam.Adam'>
Epoch: 0001 Modularity: 0.00898881 time: 0.0015s
Epoch: 0051 Modularity: 0.04986063 time: 0.0013s
Epoch: 0101 Modularity: 0.09466974 time: 0.0011s
Epoch: 0151 Modularity: 0.25447923 time: 0.0012s
Epoch: 0201 Modularity: 0.29744458 time: 0.0011s
Epoch: 0251 Modularity: 0.36287081 time: 0.0010s
Epoch: 0301 Modularity: 0.39426839 time: 0.0010s
Epoch: 0351 Modularity: 0.39426839 time: 0.0010s
Epoch: 0401 Modularity: 0.39426839 time: 0.0010s
Epoch: 0451 Modularity: 0.39426839 time: 0.0010s
Epoch: 0501 Modularity: 0.39426839 time: 0.0010s
Epoch: 0551 Modularity: 0.39426839 time: 0.0011s
Epoch: 0601 Modularity: 0.39426839 time: 0.0012s
Epoch: 0651 Modularity: 0.39426839 time: 0.0011s
Epoch: 0701 Modularity: 0.39426839 time: 0.0013s
Epoch: 0751 Modularity: 0.39426839 time: 0.0010s
Epoch: 0801 Modularity: 0.39426839 time: 0.0013s
Epoch: 0851 Modularity: 0.39426839 time: 0.0012s
Epoch: 0901 Modularity: 0.39426839 time: 0.0010s
Ep

# 1-Layer

## Full

In [26]:
network = get_network("Dolphins Social Network")
new_features, new_mod, combo_mod = run_experiment('1Lq', network, optim.Adam, n_epochs=6000, partition_method='rand', embed_dim=3, seed=temp_seed)

->>starting 1Lq optimization using <class 'torch.optim.adam.Adam'>
Combo's modularity = 0.52679878, modularity before perturbation = -0.04902892
Epoch: 0001 Modularity: 0.01451679 time: 0.0011s
Epoch: 0301 Modularity: 0.46793583 time: 0.0003s
Epoch: 0601 Modularity: 0.49992090 time: 0.0005s
Epoch: 0901 Modularity: 0.50297642 time: 0.0003s
Epoch: 1201 Modularity: 0.50507432 time: 0.0003s
Epoch: 1501 Modularity: 0.50758630 time: 0.0003s
Epoch: 1801 Modularity: 0.50899863 time: 0.0003s
Epoch: 2101 Modularity: 0.51114732 time: 0.0003s
Epoch: 2401 Modularity: 0.51380873 time: 0.0003s
Epoch: 2701 Modularity: 0.51512992 time: 0.0003s
Epoch: 3001 Modularity: 0.51512992 time: 0.0003s
Epoch: 3301 Modularity: 0.51512992 time: 0.0003s
Epoch: 3601 Modularity: 0.51512992 time: 0.0003s
Epoch: 3901 Modularity: 0.51512992 time: 0.0003s
Epoch: 4201 Modularity: 0.51512992 time: 0.0003s
Epoch: 4501 Modularity: 0.51512992 time: 0.0003s
Epoch: 4801 Modularity: 0.51512992 time: 0.0003s
Epoch: 5101 Modularity

In [27]:
old_mod = -1
while new_mod > old_mod:
    old_mod = new_mod
    new_features, new_mod, _ = run_experiment('1Lq', network, optim.Adam, n_epochs=10000, init_features=new_features)

->>starting 1Lq optimization using <class 'torch.optim.adam.Adam'>
Epoch: 0001 Modularity: 0.51417178 time: 0.0007s
Epoch: 0501 Modularity: 0.51512992 time: 0.0003s
Epoch: 1001 Modularity: 0.51512992 time: 0.0003s
Epoch: 1501 Modularity: 0.51512992 time: 0.0003s
Epoch: 2001 Modularity: 0.51512992 time: 0.0003s
Epoch: 2501 Modularity: 0.51512992 time: 0.0003s
Epoch: 3001 Modularity: 0.51512992 time: 0.0003s
Epoch: 3501 Modularity: 0.51512992 time: 0.0003s
Epoch: 4001 Modularity: 0.51512992 time: 0.0004s
Epoch: 4501 Modularity: 0.51512992 time: 0.0003s
Epoch: 5001 Modularity: 0.51512992 time: 0.0003s
Epoch: 5501 Modularity: 0.51512992 time: 0.0003s
Epoch: 6001 Modularity: 0.51512992 time: 0.0003s
Epoch: 6501 Modularity: 0.51512992 time: 0.0003s
Epoch: 7001 Modularity: 0.51512992 time: 0.0003s
Epoch: 7501 Modularity: 0.51512992 time: 0.0003s
Epoch: 8001 Modularity: 0.51512992 time: 0.0003s
Epoch: 8501 Modularity: 0.51512992 time: 0.0003s
Epoch: 9001 Modularity: 0.51512992 time: 0.0003s
Ep

## Diagonal

In [29]:
network = get_network("Dolphins Social Network")
new_features, new_mod, combo_mod = run_experiment('1Dq', network, optim.Adam, n_epochs=20000, partition_method='rand', embed_dim=3, seed=temp_seed)

->>starting 1Dq optimization using <class 'torch.optim.adam.Adam'>
Combo's modularity = 0.52679878, modularity before perturbation = -0.04902892
Epoch: 0001 Modularity: 0.01451679 time: 0.0009s
Epoch: 1001 Modularity: 0.25572941 time: 0.0003s
Epoch: 2001 Modularity: 0.26890120 time: 0.0003s
Epoch: 3001 Modularity: 0.28000504 time: 0.0003s
Epoch: 4001 Modularity: 0.28911874 time: 0.0003s
Epoch: 5001 Modularity: 0.29272267 time: 0.0003s
Epoch: 6001 Modularity: 0.29703850 time: 0.0003s
Epoch: 7001 Modularity: 0.30034769 time: 0.0003s
Epoch: 8001 Modularity: 0.30283225 time: 0.0003s
Epoch: 9001 Modularity: 0.30586845 time: 0.0003s
Epoch: 10001 Modularity: 0.30970168 time: 0.0003s
Epoch: 11001 Modularity: 0.31297675 time: 0.0003s
Epoch: 12001 Modularity: 0.31512338 time: 0.0003s
Epoch: 13001 Modularity: 0.31826663 time: 0.0003s
Epoch: 14001 Modularity: 0.31938797 time: 0.0003s
Epoch: 15001 Modularity: 0.32087871 time: 0.0003s
Epoch: 16001 Modularity: 0.32224119 time: 0.0003s
Epoch: 17001 Mo

In [180]:
old_mod = -1
while new_mod > old_mod:
    old_mod = new_mod
    new_features, new_mod, _ = run_experiment('1Dq', network, optim.Adam, n_epochs=10000, init_features=new_features)

->>starting 1Dq optimization using <class 'torch.optim.adam.Adam'>
Combo's modularity = 0.52679878, modularity before perturbation = 0.26804712
Epoch: 0001 Modularity: 0.34616256 time: 0.0006s
Epoch: 0501 Modularity: 0.39649016 time: 0.0003s
Epoch: 1000 Modularity: 0.40041748 time: 0.0003s
Epoch: 1001 Modularity: 0.40042800 time: 0.0008s
Epoch: 1501 Modularity: 0.40449110 time: 0.0003s
Epoch: 2001 Modularity: 0.40783942 time: 0.0003s
Epoch: 2501 Modularity: 0.40837604 time: 0.0003s
Epoch: 3001 Modularity: 0.40917954 time: 0.0003s
Epoch: 3501 Modularity: 0.41063905 time: 0.0003s
Epoch: 4001 Modularity: 0.41161823 time: 0.0003s
Epoch: 4501 Modularity: 0.41162711 time: 0.0003s
Epoch: 5001 Modularity: 0.41163835 time: 0.0003s
Epoch: 5501 Modularity: 0.41165212 time: 0.0003s
Epoch: 6001 Modularity: 0.41166881 time: 0.0003s
Epoch: 6501 Modularity: 0.41168898 time: 0.0003s
Epoch: 7001 Modularity: 0.41170946 time: 0.0003s
Epoch: 7501 Modularity: 0.41173339 time: 0.0004s
Epoch: 8001 Modularity:

## Random tries

### 1 Full Layer using modularity matrix and embeddings

In [30]:
results_1FullLayerModEmbed = random_trials('1Lq', embed_dim=3)

		Starting processing net karate
	->>Starting trial  0
->>starting 1Lq optimization using <class 'torch.optim.adam.Adam'>
Combo's modularity = 0.41978961, modularity before perturbation = -0.05728139
Epoch: 0001 Modularity: 0.01062685 time: 0.0006s
Epoch: 0101 Modularity: 0.29741019 time: 0.0003s
Epoch: 0201 Modularity: 0.35837355 time: 0.0003s
Epoch: 0301 Modularity: 0.37616596 time: 0.0003s
Epoch: 0401 Modularity: 0.37871704 time: 0.0003s
Epoch: 0501 Modularity: 0.37963891 time: 0.0002s
Epoch: 0601 Modularity: 0.38030916 time: 0.0003s
Epoch: 0701 Modularity: 0.38127351 time: 0.0003s
Epoch: 0801 Modularity: 0.38271630 time: 0.0003s
Epoch: 0901 Modularity: 0.38530526 time: 0.0003s
Epoch: 1001 Modularity: 0.38944584 time: 0.0003s
Epoch: 1101 Modularity: 0.38957557 time: 0.0003s
Epoch: 1201 Modularity: 0.38977095 time: 0.0002s
Epoch: 1301 Modularity: 0.38979292 time: 0.0003s
Epoch: 1401 Modularity: 0.38979292 time: 0.0003s
Epoch: 1501 Modularity: 0.38979292 time: 0.0002s
Epoch: 1601 Modu

### 1 Full Layer using modularity matrix

In [162]:
results_1FullLayerMod = random_trials('1Lq')

		Starting processing net karate
	->>Starting trial  0
->>starting 1Lq optimization using <class 'torch.optim.adam.Adam'>
Combo's modularity = 0.41978961, modularity before perturbation = -0.05728139
Epoch: 0001 Modularity: -0.01924488 time: 0.0006s
Epoch: 0101 Modularity: 0.10864870 time: 0.0003s
Epoch: 0201 Modularity: 0.19368865 time: 0.0003s
Epoch: 0301 Modularity: 0.23791577 time: 0.0003s
Epoch: 0401 Modularity: 0.25138614 time: 0.0003s
Epoch: 0501 Modularity: 0.25630638 time: 0.0003s
Epoch: 0601 Modularity: 0.26673901 time: 0.0004s
Epoch: 0701 Modularity: 0.26830539 time: 0.0003s
Epoch: 0801 Modularity: 0.26954684 time: 0.0003s
Epoch: 0901 Modularity: 0.27070317 time: 0.0003s
Epoch: 1000 Modularity: 0.27154917 time: 0.0003s
Epoch: 1001 Modularity: 0.27154917 time: 0.0006s
Epoch: 1101 Modularity: 0.27181795 time: 0.0003s
Epoch: 1201 Modularity: 0.27198994 time: 0.0003s
Epoch: 1301 Modularity: 0.27223852 time: 0.0003s
Epoch: 1401 Modularity: 0.27252820 time: 0.0003s
Epoch: 1501 Mod

### 1 Diagonal layer

In [163]:
results_1DiagLayerMod = random_trials('1Dq')

		Starting processing net karate
	->>Starting trial  0
->>starting 1Dq optimization using <class 'torch.optim.adam.Adam'>
Combo's modularity = 0.41978961, modularity before perturbation = -0.05728139
Epoch: 0001 Modularity: -0.01924488 time: 0.0006s
Epoch: 0101 Modularity: 0.06373797 time: 0.0003s
Epoch: 0201 Modularity: 0.09963375 time: 0.0004s
Epoch: 0301 Modularity: 0.12489012 time: 0.0009s
Epoch: 0401 Modularity: 0.15458772 time: 0.0003s
Epoch: 0501 Modularity: 0.16605590 time: 0.0004s
Epoch: 0601 Modularity: 0.17239553 time: 0.0003s
Epoch: 0701 Modularity: 0.17696609 time: 0.0003s
Epoch: 0801 Modularity: 0.18302588 time: 0.0003s
Epoch: 0901 Modularity: 0.19411090 time: 0.0003s
Epoch: 1000 Modularity: 0.21106367 time: 0.0003s
Epoch: 1001 Modularity: 0.21133481 time: 0.0006s
Epoch: 1101 Modularity: 0.22529913 time: 0.0003s
Epoch: 1201 Modularity: 0.22793940 time: 0.0003s
Epoch: 1301 Modularity: 0.23066120 time: 0.0003s
Epoch: 1401 Modularity: 0.23173670 time: 0.0003s
Epoch: 1501 Mod

# Results


In [167]:
results.to_csv("new_results.csv")

In [90]:
results = pd.DataFrame(columns=['Method']+["karate", "David Copperfield","Jazz Musicians","Dolphins Social Network"]+['time'])
results = results.append(results_1FullLayerMod, ignore_index=True)
results

Method    karate  David Copperfield  Jazz Musicians  \
0  1Lq with 5 random starts  0.395874           0.284606        0.444469   

   Dolphins Social Network        time  
0                 0.522013  339.553605

In [166]:
results = pd.DataFrame(columns=['Method']+net_names+['time'])
results = results.append(results_combo, ignore_index=True)
results = results.append(results_GNNS, ignore_index=True)
results = results.append(results_simple, ignore_index=True)
results = results.append(results_1DiagLayerMod, ignore_index=True)
results = results.append(results_1FullLayerMod, ignore_index=True)
results

Method    karate  David Copperfield  Jazz Musicians  \
0                        Combo  0.419790           0.308742        0.444469   
1    GNNS with 5 random starts  0.415790           0.296294        0.444078   
2  simple with 5 random starts  0.419790           0.301149        0.444259   
3     1Dq with 5 random starts  0.402038           0.290198        0.444315   
4     1Lq with 5 random starts  0.402038           0.295579        0.444349   

   Dolphins Social Network        time  
0                 0.526799          -1  
1                 0.525562   16.270827  
2                 0.526799  184.769144  
3                 0.510660  424.576771  
4                 0.520292  465.359739

## Best results that I've seen so far
### rand GNNS
- Best mod for net karate is 0.41696786880493164
- Best mod for net David Copperfield is 0.29637816548347473
- Best mod for net Jazz Musicians is 0.4441315531730652
- Best mod for net Dolphins Social Network is 0.5213608741760254

### rand simple
- Best mod for net karate is 0.4197896718978882
- Best mod for net David Copperfield is 0.30114877223968506
- Best mod for net Jazz Musicians is 0.44425898790359497
- Best mod for net Dolphins Social Network is 0.5267987251281738


### rand 1L adj_norm
- Best mod for net karate is 0.3878205418586731
- Best mod for net David Copperfield is 0.23354023694992065
- Best mod for net Jazz Musicians is 0.4232749938964844
- Best mod for net Dolphins Social Network is 0.4712923765182495

### rand 1L Q_norm
- Best mod for net karate is 0.39618340134620667
- Best mod for net David Copperfield is 0.26255524158477783
- Best mod for net Jazz Musicians is 0.432380348443985
- Best mod for net Dolphins Social Network is 0.48200228810310364

### rand 1L Q_norm Diag
- Best mod for net karate is 0.4020381569862366
- Best mod for net David Copperfield is 0.2917425334453583
- Best mod for net Jazz Musicians is 0.4443153738975525
- Best mod for net Dolphins Social Network is 0.5106601715087891
